This file can be used to reproduce figures 2-4 from the paper (and equivalent figures). For details on the data used, please see the main reproducibility document

In [ ]:
import numpy as np
import pickle
import pandas as pd
from functools import partial
import glob
import seaborn as sbs
import matplotlib.pyplot as plt

from scipy.stats import kendalltau, rankdata

font = {'size'   : 24}

plt.rc('font', **font)

#Font-requirement for GECCO
import matplotlib
matplotlib.rcParams['pdf.fonttype'] = 42
matplotlib.rcParams['ps.fonttype'] = 42

In [ ]:
dt = pd.DataFrame()
for f in glob.glob("Alg_Restart_Csv/*"):
    dt_temp = pd.read_csv(f, index_col=0)
    dt = dt.append(dt_temp)

In [ ]:
dt = dt.reset_index()

In [ ]:
ids = np.array(dt['ID'])
records = [str.split(x,'_') for x in ids]
dt_info = pd.DataFrame.from_records(records, columns=['Algname', 'S'])

In [ ]:
dt = dt_info.merge(dt, left_index=True, right_index=True)

In [ ]:
dt

In [ ]:
dt_base = dt[dt['DIM'] == 10]

In [ ]:
dt_base['geometric mean'][dt_base['geometric mean'] < 1e-8] = 1e-8

In [ ]:
palette = dict(zip(np.unique(dt_base['Algname']), sbs.color_palette(n_colors=len(np.unique(dt_base['Algname'])))))

In [ ]:
plt.figure(figsize=(16,9))
dt_static = dt_base[dt_base['S'] == 'S0']
dt_sw = dt_base[dt_base['S'] != 'S0']

sbs.stripplot(data=dt_sw, x='funcId', y='geometric mean', hue='Algname', palette=palette)
ax = sbs.stripplot(data=dt_static, x='funcId', y='geometric mean', hue='Algname', marker='D', size=10, alpha=0.6, palette=palette)

handles, labels = ax.get_legend_handles_labels()

plt.yscale('log')
plt.ylabel('f(x)')
plt.xlabel('Function ID')
# When creating the legend, only use the first two elements
# to effectively remove the last two.
l = plt.legend(handles[0:5], labels[0:5], bbox_to_anchor=(1.05, 1), loc=2, borderaxespad=0., fontsize=14)
plt.tight_layout()
# plt.savefig("Paper_Figures/Warmstart_Impact_updated.pdf")

In [ ]:
stat_vals = []
for i in range(600):
    item = dt_sw.iloc[i]
    item_stat = dt_static[(dt_static['funcId'] == item['funcId']) & (dt_static['Algname'] == item['Algname'])]['geometric mean']
    stat_vals.append(np.array(item_stat)[0])

In [ ]:
dt_sw['stat_val'] = stat_vals

In [ ]:
dt_sw['relative_log'] = np.log(dt_sw['geometric mean']) - np.log(dt_sw['stat_val'])

In [ ]:
dt_sw['relative'] = dt_sw['geometric mean'] / dt_sw['stat_val']

In [ ]:
plt.figure(figsize=(16,9))

sbs.boxplot(data=dt_sw, x='Algname', y='relative_log', hue='S')#, palette=palette)

handles, labels = ax.get_legend_handles_labels()

# plt.yscale('log')
plt.ylabel('Log difference')
plt.xlabel('Algorithm Name')
plt.ylim(-5,5)
plt.axhline(0, ls=':', c='k')
plt.xticks(rotation=-20)
# When creating the legend, only use the first two elements
# to effectively remove the last two.
# l = plt.legend(handles[0:5], labels[0:5], bbox_to_anchor=(1.05, 1), loc=2, borderaxespad=0., fontsize=14)
plt.legend(fontsize=18, title='Switch point')
plt.tight_layout()
plt.savefig("Paper_Figures/Relative_A1_restart_v6.pdf")

In [ ]:
plt.figure(figsize=(16,9))

sbs.boxplot(data=dt_sw, x='funcId', y='relative', hue='Algname', palette=palette)

handles, labels = ax.get_legend_handles_labels()

# plt.yscale('log')
plt.ylabel('Relative difference (precision / static precision)')
plt.xlabel('Function ID')
plt.ylim(0,2)
plt.axhline(1, ls=':', c='k')
# When creating the legend, only use the first two elements
# to effectively remove the last two.
l = plt.legend(handles[0:5], labels[0:5], bbox_to_anchor=(1.05, 1), loc=2, borderaxespad=0., fontsize=14)
plt.tight_layout()
plt.savefig("Paper_Figures/Relative_A1_restart_v5.pdf")

In [ ]:
dt_overall = pd.DataFrame()
for f in glob.glob("/mnt/e/Research/SPECIES/verification_dt/*"):
    dt_temp = pd.read_csv(f, index_col=0)
    dt_overall = dt_overall.append(dt_temp)

dt_overall = dt_overall.reset_index()
records = [str.split(x,'_') for x in dt_overall['ID']]
dt_info = pd.DataFrame.from_records(records, columns=['A1', 'A2', 'S'])
dt_overall = dt_info.merge(dt_overall, left_index=True, right_index=True)


fxs = np.array(dt_overall['f(x)'])
fxs[fxs<1e-9] = 1e-9
dt_overall['f(x)'] = fxs

agg_dt = dt_overall.groupby(['funcId', 'ID', 'DIM', 'A1', 'A2', 'S']).agg(lambda x: np.exp(np.mean(np.log(x)))).reset_index()

VBS = agg_dt[agg_dt['A2'] == 'None'].sort_values("f(x)").groupby(["funcId", 'DIM'], as_index=False).first()

dt_agg_with_impr = pd.DataFrame()
for fid in range(1,25):
    for dim in [10,20]:
        val = VBS[(VBS['funcId'] == fid) & (VBS['DIM'] == dim)]
        vbs_fx = np.array(val['f(x)'])[0]
        agg_dt_temp = agg_dt[(agg_dt['funcId'] == fid) & (agg_dt['DIM'] == dim)]
        agg_dt_temp = agg_dt_temp[agg_dt_temp['A2'] != 'None']
        agg_dt_temp['impr'] = np.array(1-agg_dt_temp['f(x)']/vbs_fx)
        dt_agg_with_impr = dt_agg_with_impr.append(agg_dt_temp)

In [ ]:
dt_overall = pd.DataFrame()
for f in glob.glob("../../Temp/verification_dt/*"):
    dt_temp = pd.read_csv(f, index_col=0)
    dt_overall = dt_overall.append(dt_temp)

dt_overall = dt_overall.reset_index()
records = [str.split(x,'_') for x in dt_overall['ID']]
dt_info = pd.DataFrame.from_records(records, columns=['A1', 'A2', 'S'])
dt_overall = dt_info.merge(dt_overall, left_index=True, right_index=True)


fxs = np.array(dt_overall['f(x)'])
fxs[fxs<1e-9] = 1e-9
dt_overall['f(x)'] = fxs

agg_dt = dt_overall.groupby(['funcId', 'ID', 'DIM', 'A1', 'A2', 'S']).agg(lambda x: np.exp(np.mean(np.log(x)))).reset_index()

VBS = agg_dt[agg_dt['A2'] == 'None'].sort_values("f(x)").groupby(["funcId", 'DIM'], as_index=False).first()

dt_agg_with_impr = pd.DataFrame()
for fid in range(1,25):
    for dim in [10,20]:
        val = VBS[(VBS['funcId'] == fid) & (VBS['DIM'] == dim)]
        vbs_fx = np.array(val['f(x)'])[0]
        agg_dt_temp = agg_dt[(agg_dt['funcId'] == fid) & (agg_dt['DIM'] == dim)]
        agg_dt_temp = agg_dt_temp[agg_dt_temp['A2'] != 'None']
        agg_dt_temp['impr'] = np.array(1-agg_dt_temp['f(x)']/vbs_fx)
        dt_agg_with_impr = dt_agg_with_impr.append(agg_dt_temp)

In [ ]:
real_splits = [int(x[1:]) for x in dt_agg_with_impr['S']]
dt_agg_with_impr['S'] = real_splits

In [ ]:
plt.figure(figsize=(16,6))
ax = sbs.scatterplot(data=dt_agg_with_impr[dt_agg_with_impr['DIM'] == 20], x='funcId', y='S', 
                     hue='impr', palette='RdBu_r', hue_norm=(-1,1), s=250, 
                     edgecolor='k', linewidth=0.2)
for i in range(1,24):
    plt.axvline(i+0.5, ls=':', c='k', lw=1)

norm = plt.Normalize(-1,1)
sm = plt.cm.ScalarMappable(cmap="RdBu_r", norm=norm)
sm.set_array([])

# Remove the legend and add a colorbar
ax.get_legend().remove()
ax.figure.colorbar(sm)
# plt.legend(fontsize=12)
# plt.colorbar()
plt.yscale('log')
plt.xlim(0.5,24.5)
plt.xticks(range(1,25), range(1,25))
plt.ylabel("Splitpoint")
plt.tight_layout()
plt.savefig("Paper_Figures/Spoint_distr_20D_rel_impr_fx_v3.pdf")

In [ ]:
plt.figure(figsize=(16,10))
sbs.stripplot(data=dt_agg_with_impr, x='funcId', y='impr', hue = 'DIM')
plt.ylim(-1.5,1.5)
plt.axhline(0, ls='-', c='k')
for i in range(23):
    plt.axvline(i+0.5, ls=':', c='k', lw=1)
plt.tight_layout()
plt.savefig("Paper_Figures/Mean_Impr_fx.pdf")
plt.show()